<a href="https://colab.research.google.com/github/jusbinm/Plant-Recognition-using-inception-model/blob/master/model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!wget http://leafsnap.com/static/dataset/leafsnap-dataset.tar

--2019-03-07 05:07:35--  http://leafsnap.com/static/dataset/leafsnap-dataset.tar
Resolving leafsnap.com (leafsnap.com)... 128.59.23.133
Connecting to leafsnap.com (leafsnap.com)|128.59.23.133|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1023416320 (976M) [application/x-tar]
Saving to: ‘leafsnap-dataset.tar’

leafsnap-dataset.ta 100%[===================>] 976.01M  79.7MB/s    in 14s     

2019-03-07 05:07:54 (68.3 MB/s) - ‘leafsnap-dataset.tar’ saved [1023416320/1023416320]



In [0]:
!tar -xvf leafsnap-dataset.tar

dataset/images/
dataset/images/field/
dataset/images/field/ulmus_glabra/
dataset/images/field/ulmus_glabra/13291717341164.jpg
dataset/images/field/ulmus_glabra/13291717347502.jpg
dataset/images/field/ulmus_glabra/13291717349337.jpg
dataset/images/field/ulmus_glabra/13291717347622.jpg
dataset/images/field/ulmus_glabra/13291717342603.jpg
dataset/images/field/ulmus_glabra/13291717345038.jpg
dataset/images/field/ulmus_glabra/13291717341614.jpg
dataset/images/field/ulmus_glabra/13291717345731.jpg
dataset/images/field/ulmus_glabra/13291717348788.jpg
dataset/images/field/ulmus_glabra/13291717349064.jpg
dataset/images/field/ulmus_glabra/13291717343709.jpg
dataset/images/field/ulmus_glabra/13291717344393.jpg
dataset/images/field/ulmus_glabra/13291717347291.jpg
dataset/images/field/ulmus_glabra/13291717343335.jpg
dataset/images/field/ulmus_glabra/13291717347953.jpg
dataset/images/field/ulmus_glabra/13291717348659.jpg
dataset/images/field/ulmus_glabra/13291717348826.jpg
dataset/images/field/ulmus

In [0]:
import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np
import torchvision
from torchvision import datasets, models, transforms
import matplotlib.pyplot as plt
import time
import os
import copy
print("PyTorch Version: ",torch.__version__)
print("Torchvision Version: ",torchvision.__version__)

PyTorch Version:  1.0.1.post2
Torchvision Version:  0.2.2


In [0]:
# Top level data directory. Here we assume the format of the directory conforms
#   to the ImageFolder structure
data_dir = "images"

# Models to choose from [resnet, alexnet, vgg, squeezenet, densenet, inception]
model_name = "inception"

# Number of classes in the dataset
num_classes = 13

# Batch size for training (change depending on how much memory you have)
batch_size = 32

# Number of epochs to train for
num_epochs = 2000

# Flag for feature extracting. When False, we finetune the whole model,
#   when True we only update the reshaped layer params
feature_extract = True

In [0]:
!unzip images.zip

Archive:  images.zip
   creating: images/
   creating: images/val/
   creating: images/val/acer_pseudoplatanus/
  inflating: images/val/acer_pseudoplatanus/1249580294_0000.jpg  
  inflating: images/val/acer_pseudoplatanus/1259118878_0009.jpg  
  inflating: images/val/acer_pseudoplatanus/1249580294_0002.jpg  
  inflating: images/val/acer_pseudoplatanus/1252646935_0001.jpg  
  inflating: images/val/acer_pseudoplatanus/1249580294_0001.jpg  
  inflating: images/val/acer_pseudoplatanus/1249580294_0003.jpg  
  inflating: images/val/acer_pseudoplatanus/1259118878_0064.jpg  
  inflating: images/val/acer_pseudoplatanus/1259118878_0003.jpg  
  inflating: images/val/acer_pseudoplatanus/1252646935_0000.jpg  
  inflating: images/val/acer_pseudoplatanus/1259118878_0100.jpg  
  inflating: images/val/acer_pseudoplatanus/1252646935_0002.jpg  
  inflating: images/val/acer_pseudoplatanus/1252646935_0004.jpg  
  inflating: images/val/acer_pseudoplatanus/1252646935_0003.jpg  
  inflating: images/val/acer_p

In [0]:
# Top level data directory. Here we assume the format of the directory conforms
#   to the ImageFolder structure
data_dir = "./images"

# Models to choose from [resnet, alexnet, vgg, squeezenet, densenet, inception]
model_name = "inception"

# Number of classes in the dataset
num_classes = 13

# Batch size for training (change depending on how much memory you have)
batch_size = 8

# Number of epochs to train for
num_epochs = 15

# Flag for feature extracting. When False, we finetune the whole model,
#   when True we only update the reshaped layer params
feature_extract = True

In [0]:
def train_model(model, dataloaders, criterion, optimizer, num_epochs=25, is_inception=False):
    since = time.time()

    val_acc_history = []

    best_model_wts = copy.deepcopy(model.state_dict())
    best_acc = 0.0

    for epoch in range(num_epochs):
        print('Epoch {}/{}'.format(epoch, num_epochs - 1))
        print('-' * 10)

        # Each epoch has a training and validation phase
        for phase in ['train', 'val']:
            if phase == 'train':
                model.train()  # Set model to training mode
            else:
                model.eval()   # Set model to evaluate mode

            running_loss = 0.0
            running_corrects = 0

            # Iterate over data.
            for inputs, labels in dataloaders[phase]:
                inputs = inputs.to(device)
                labels = labels.to(device)

                # zero the parameter gradients
                optimizer.zero_grad()

                # forward
                # track history if only in train
                with torch.set_grad_enabled(phase == 'train'):
                    # Get model outputs and calculate loss
                    # Special case for inception because in training it has an auxiliary output. In train
                    #   mode we calculate the loss by summing the final output and the auxiliary output
                    #   but in testing we only consider the final output.
                    if is_inception and phase == 'train':
                        # From https://discuss.pytorch.org/t/how-to-optimize-inception-model-with-auxiliary-classifiers/7958
                        outputs, aux_outputs = model(inputs)
                        loss1 = criterion(outputs, labels)
                        loss2 = criterion(aux_outputs, labels)
                        loss = loss1 + 0.4*loss2
                    else:
                        outputs = model(inputs)
                        loss = criterion(outputs, labels)

                    _, preds = torch.max(outputs, 1)

                    # backward + optimize only if in training phase
                    if phase == 'train':
                        loss.backward()
                        optimizer.step()

                # statistics
                running_loss += loss.item() * inputs.size(0)
                running_corrects += torch.sum(preds == labels.data)

            epoch_loss = running_loss / len(dataloaders[phase].dataset)
            epoch_acc = running_corrects.double() / len(dataloaders[phase].dataset)

            print('{} Loss: {:.4f} Acc: {:.4f}'.format(phase, epoch_loss, epoch_acc))

            # deep copy the model
            if phase == 'val' and epoch_acc > best_acc:
                best_acc = epoch_acc
                best_model_wts = copy.deepcopy(model.state_dict())
            if phase == 'val':
                val_acc_history.append(epoch_acc)

        print()

    time_elapsed = time.time() - since
    print('Training complete in {:.0f}m {:.0f}s'.format(time_elapsed // 60, time_elapsed % 60))
    print('Best val Acc: {:4f}'.format(best_acc))

    # load best model weights
    model.load_state_dict(best_model_wts)
    return model, val_acc_history

In [0]:
def set_parameter_requires_grad(model, feature_extracting):
    if feature_extracting:
        for param in model.parameters():
            param.requires_grad = False

In [0]:
def initialize_model(model_name, num_classes, feature_extract, use_pretrained=True):
        model_ft = None
        input_size = 0 
      
        model_ft = models.inception_v3(pretrained=use_pretrained)    #change in code initially the model should be initialized then print
        #print(model_ft) 
        set_parameter_requires_grad(model_ft, feature_extract)
        # Handle the auxilary net
        num_ftrs = model_ft.AuxLogits.fc.in_features
        model_ft.AuxLogits.fc = nn.Linear(num_ftrs, num_classes)
        # Handle the primary net
        num_ftrs = model_ft.fc.in_features
        model_ft.fc = nn.Linear(num_ftrs,num_classes)
        input_size = 299
        return model_ft, input_size

# Initialize the model for this run
model_ft, input_size = initialize_model(model_name, num_classes, feature_extract, use_pretrained=True)

# Print the model we just instantiated
print(model_ft)

Inception3(
  (Conv2d_1a_3x3): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2a_3x3): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2b_3x3): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_3b_1x1): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_4a_3x3): BasicConv2d(
    (conv): Conv2d(80, 192, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(192, eps=0.001, momentum=0.1, affine=True, t

In [0]:
# Data augmentation and normalization for training
# Just normalization for validation
data_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(input_size),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'val': transforms.Compose([
        transforms.Resize(input_size),
        transforms.CenterCrop(input_size),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
}

print("Initializing Datasets and Dataloaders...")

# Create training and validation datasets
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x), data_transforms[x]) for x in ['train', 'val']}
# Create training and validation dataloaders
dataloaders_dict = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=batch_size, shuffle=True, num_workers=4) for x in ['train', 'val']}

# Detect if we have a GPU available
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

Initializing Datasets and Dataloaders...


In [0]:
# Send the model to GPU
model_ft = model_ft.to(device)

# Gather the parameters to be optimized/updated in this run. If we are
#  finetuning we will be updating all parameters. However, if we are
#  doing feature extract method, we will only update the parameters
#  that we have just initialized, i.e. the parameters with requires_grad
#  is True.
params_to_update = model_ft.parameters()
print("Params to learn:")
if feature_extract:
    params_to_update = []
    for name,param in model_ft.named_parameters():
        if param.requires_grad == True:
            params_to_update.append(param)
            print("\t",name)
else:
    for name,param in model_ft.named_parameters():
        if param.requires_grad == True:
            print("\t",name)

# Observe that all parameters are being optimized
optimizer_ft = optim.SGD(params_to_update, lr=0.001, momentum=0.9)

Params to learn:
	 AuxLogits.fc.weight
	 AuxLogits.fc.bias
	 fc.weight
	 fc.bias


In [0]:
# Setup the loss fxn
criterion = nn.CrossEntropyLoss()

# Train and evaluate
model_ft, hist = train_model(model_ft, dataloaders_dict, criterion, optimizer_ft, num_epochs=num_epochs, is_inception=(model_name=="inception"))

Epoch 0/14
----------
train Loss: 3.2221 Acc: 0.2373
val Loss: 1.8846 Acc: 0.5314

Epoch 1/14
----------
train Loss: 2.3820 Acc: 0.5051
val Loss: 1.4990 Acc: 0.6450

Epoch 2/14
----------
train Loss: 1.9392 Acc: 0.6329
val Loss: 1.2394 Acc: 0.7769

Epoch 3/14
----------
train Loss: 1.6890 Acc: 0.6836
val Loss: 1.0027 Acc: 0.8316

Epoch 4/14
----------
train Loss: 1.3930 Acc: 0.7627
val Loss: 0.8689 Acc: 0.8256

Epoch 5/14
----------
train Loss: 1.2624 Acc: 0.7627
val Loss: 0.7313 Acc: 0.8722

Epoch 6/14
----------
train Loss: 1.1421 Acc: 0.7972
val Loss: 0.6489 Acc: 0.9128

Epoch 7/14
----------
train Loss: 1.1262 Acc: 0.7992
val Loss: 0.6284 Acc: 0.8905

Epoch 8/14
----------
train Loss: 1.0198 Acc: 0.7992
val Loss: 0.5284 Acc: 0.9513

Epoch 9/14
----------
train Loss: 1.0374 Acc: 0.7606
val Loss: 0.5112 Acc: 0.9249

Epoch 10/14
----------
train Loss: 0.8708 Acc: 0.8519
val Loss: 0.4604 Acc: 0.9473

Epoch 11/14
----------
train Loss: 0.8717 Acc: 0.8580
val Loss: 0.4536 Acc: 0.9108

Ep

In [0]:
from PIL import Image
import torchvision.transforms as transforms
standard_normalization = transforms.Normalize(mean=[0.485, 0.456, 0.406],
                                              std=[0.229, 0.224, 0.225])
def load_input_image(img_path):    
    image = Image.open(img_path).convert('RGB')
    prediction_transform = transforms.Compose([transforms.Resize(size=(224, 224)),
                                     transforms.ToTensor(), 
                                     standard_normalization])

    # discard the transparent, alpha channel (that's the :3) and add the batch dimension
    image = prediction_transform(image)[:3,:,:].unsqueeze(0)
    return image

In [0]:
def predict_teeth_transfer(model, img_path):
    # load the image and return the predicted teeth 
   
    img = load_input_image(img_path)
    model = model.cpu()
    model.eval()
    idx = torch.argmax(model(img))
    
    return idx

In [53]:
img_path = "/content/class 3.jpg"
  
 
predict_teeth_transfer(model_ft,"/content/class 3.jpg")

tensor(2)

In [54]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
model_save_name = 'classifier.pt'
path = F"/content/gdrive/My Drive/{model_save_name}" 
torch.save(model_ft.state_dict(), path)